In [1]:
# Imports y carga
import pandas as pd
import geopandas as gpd
from pathlib import Path
import folium
from folium.plugins import MarkerCluster
import os, sys
import requests
from io import BytesIO
import logging  

In [2]:

cwd = Path.cwd()
repo_root = None
for p in [cwd] + list(cwd.parents):
    if (p / "pyproject.toml").exists():
        repo_root = p
        break

if repo_root:
    os.chdir(repo_root)
    print("Changed working dir to repo root:", repo_root)
else:
    print("Repo root with pyproject.toml not found. Current cwd remains:", cwd)
    print("You can also set repo root manually, e.g.: os.chdir('/home/tepeve/personal/repos/ba_ooh_ads')")
print("Now cwd:", Path.cwd())
print("Python executable:", sys.executable)
print(".venv exists here?:", (Path('.venv').exists()))

Changed working dir to repo root: /home/tepeve/personal/repos/ba_ooh_ads
Now cwd: /home/tepeve/personal/repos/ba_ooh_ads
Python executable: /home/tepeve/personal/repos/ba_ooh_ads/.venv/bin/python
.venv exists here?: True


In [3]:
URL_ETAPAS = "https://cdn.buenosaires.gob.ar/datosabiertos/datasets/transporte-y-obras-publicas/viajes-etapas-transporte-publico/viajes_BAdata_20241016.csv"
df = pd.read_csv(URL_ETAPAS)

In [4]:
df.columns

Index(['id_tarjeta', 'id_viaje', 'cantidad_etapas', 'rango_horario',
       'etapas_subte', 'etapas_tren', 'etapas_colectivo',
       'longitud_origen_viaje', 'latitud_origen_viaje',
       'longitud_destino_viaje', 'latitud_destino_viaje',
       'departamento_origen_viaje', 'departamento_destino_viaje',
       'factor_expansion_viaje', 'etapas_incompletas', 'genero', 'grupo_edad'],
      dtype='object')

In [5]:
df.departamento_origen_viaje.unique()

array([6028., 6035., 6091., 6098., 6119., 6126., 6134., 6217., 2001.,
       2010., 2011., 2012., 2013., 2014., 2015., 2002., 2003., 2004.,
       2005., 2006., 2007., 2008., 2009., 6245., 6252., 6260., 6266.,
       6270., 6274., 6329., 6364., 6371., 6408., 6410., 6412., 6427.,
       6441., 6434., 6483., 6490., 6497., 6515., 6525., 6532., 6539.,
       6547., 6560., 6568., 6574., 6638., 6648., 6658., 6728., 6735.,
       6749., 6756., 6760., 6778., 6805., 6840., 6861., 6882.,   nan])

In [6]:
df['factor_expansion_viaje'].sum().astype(int)

np.int64(9000918)

In [7]:
conteo_agrupado = df.groupby('rango_horario')['factor_expansion_viaje'].sum().astype(int)
print("Conteo ponderado de registros por rango horario:")
print(conteo_agrupado)

Conteo ponderado de registros por rango horario:
rango_horario
0      29428
1      11209
2       5664
3      14544
4      89956
5     234531
6     489847
7     745762
8     559249
9     440172
10    401855
11    493842
12    721903
13    574433
14    492263
15    528291
16    664148
17    781996
18    606827
19    406463
20    316976
21    214857
22    130115
23     46575
Name: factor_expansion_viaje, dtype: int64


In [8]:
df.grupo_edad.unique()

array([ nan,  75.,  30.,  25.,  20.,  15.,  55.,  65.,  45.,  10.,  80.,
        35.,  40.,  50.,  60.,   5.,  70.,  85.,  90.,   0.,  95., 100.])

In [9]:
#https://gis.utah.gov/blog/2022-10-26-using-h3-hexes/#:~:text=Creating%20an%20H3%20Hex%20Feature,that%20dataframe%20out%20to%20disk.&text=If%20geopandas%20and%20geojson%20is,his%20process%20into%20Esri%2Dland.

# https://geographicdata.science/book/data/h3_grid/build_sd_h3_grid.html

# https://mathiasschlaeffer.medium.com/dasymetric-spatial-interpolation-in-bigquery-ebd4ca13950d

# https://data.buenosaires.gob.ar/dataset/viajes-etapas-transporte-publico

# https://github.com/alephcero/baCommuteMatrixMap?tab=readme-ov-file

# https://github.com/EL-BID/Matriz-Origen-Destino-Transporte-Publico/tree/main

# https://el-bid.github.io/UrbanTrips/primeros_pasos.html


# https://redatam.indec.gob.ar/

In [10]:
# URL_CENSO='https://www.indec.gob.ar/ftp/cuadros/territorio/codgeo/Codgeo_CABA_con_datos.zip'
URL_CENSO='https://geonode.indec.gob.ar/geoserver/ows?service=WFS&version=2.0.0&request=GetFeature&typename=geonode:radios_censales&outputFormat=shape-zip&srsName=EPSG:4326'
r = requests.get(URL_CENSO)


In [11]:
# https://portalgeoestadistico.indec.gob.ar/maps/geoportal/nota_radios_censales.pdf
gdf = gpd.read_file(BytesIO(r.content))
gdf

/home/tepeve/personal/repos/ba_ooh_ads/.venv/lib/python3.12/site-packages/pyogrio/raw.py:200: RuntimeWarning: /vsizip//vsimem/pyogrio_f11351e059684617829228e03ba16436.zip/radios_censales.shp contains polygon(s) with rings with invalid winding order. Autocorrecting them, but that shapefile should be corrected using ogr2ogr for example.
  return ogr_read(


fid     id cpr           jur    cde                    dpto cfn cro  \
0      62930  73441  06  Buenos Aires  06014  Adolfo Gonzales Chaves  10  07   
1      62931  73443  06  Buenos Aires  06014  Adolfo Gonzales Chaves  10  09   
2      62932  84384  30    Entre Ríos  30008                   Colón  10  02   
3      62933  84383  30    Entre Ríos  30008                   Colón  10  01   
4      62934  84386  30    Entre Ríos  30008                   Colón  10  04   
...      ...    ...  ..           ...    ...                     ...  ..  ..   
66510  62925  85602  34       Formosa  34056                  Pirané  19  10   
66511  62926  90692  82      Santa Fe  82070            Las Colonias  01  16   
66512  62927  90694  82      Santa Fe  82070            Las Colonias  01  18   
66513  62928  90677  82      Santa Fe  82070            Las Colonias  01  01   
66514  62929  90679  82      Santa Fe  82070            Las Colonias  01  03   

      tro  cod_indec    sag                                           geometry  
0       U  060141007  INDEC  POLYGON ((-60.10692 -38.02435, -60.10603 -38.0...  
1       U  060141009  INDEC  POLYGON ((-60.10686 -38.01983, -60.10769 -38.0...  
2       M  300081002  INDEC  POLYGON ((-58.34108 -31.85002, -58.3412 -31.85...  
3       R  300081001  INDEC  POLYGON ((-58.44641 -31.81711, -58.44892 -31.8...  
4       R  300081004  INDEC  POLYGON ((-58.29667 -31.88732, -58.29767 -31.8...  
...    ..        ...    ...                                                ...  
66510   U  340561910  INDEC  POLYGON ((-59.36693 -26.31608, -59.36566 -26.3...  
66511   M  820700116  INDEC  POLYGON ((-60.81407 -31.01508, -60.81358 -31.0...  
66512   U  820700118  INDEC  POLYGON ((-60.89256 -31.12025, -60.89233 -31.1...  
66513   U  820700101  INDEC  POLYGON ((-61.04661 -30.69956, -61.0464 -30.69...  
66514   U  820700103  INDEC  POLYGON ((-60.97403 -30.73265, -60.97269 -30.7...  

[66515 rows x 12 columns]

In [12]:
gdf_rcensales = gdf.query("cpr == '02'")     
gdf_rcensales   

fid     id cpr                              jur    cde       dpto  \
39     62969  72887  02  Ciudad Autónoma de Buenos Aires  02049   Comuna 7   
285    63215  72890  02  Ciudad Autónoma de Buenos Aires  02049   Comuna 7   
322    63252  72889  02  Ciudad Autónoma de Buenos Aires  02049   Comuna 7   
332    63262  73022  02  Ciudad Autónoma de Buenos Aires  02070  Comuna 10   
333    63263  73329  02  Ciudad Autónoma de Buenos Aires  02091  Comuna 13   
...      ...    ...  ..                              ...    ...        ...   
65357  61772  73216  02  Ciudad Autónoma de Buenos Aires  02091  Comuna 13   
65432  61847  26695  02  Ciudad Autónoma de Buenos Aires  02021   Comuna 3   
66039  62454  73333  02  Ciudad Autónoma de Buenos Aires  02091  Comuna 13   
66220  62635  73340  02  Ciudad Autónoma de Buenos Aires  02091  Comuna 13   
66465  62880  72888  02  Ciudad Autónoma de Buenos Aires  02049   Comuna 7   

      cfn cro tro  cod_indec    sag  \
39     09  05   U  020490905  INDEC   
285    09  08   U  020490908  INDEC   
322    09  07   U  020490907  INDEC   
332    02  08   U  020700208  INDEC   
333    24  10   U  020912410  INDEC   
...    ..  ..  ..        ...    ...   
65357  09  08   U  020910908  INDEC   
65432  18  11   U  020211811  INDEC   
66039  25  04   U  020912504  INDEC   
66220  28  03   U  020912803  INDEC   
66465  09  06   U  020490906  INDEC   

                                                geometry  
39     POLYGON ((-58.46718 -34.63293, -58.46579 -34.6...  
285    POLYGON ((-58.46411 -34.62926, -58.46354 -34.6...  
322    POLYGON ((-58.46311 -34.63168, -58.46297 -34.6...  
332    POLYGON ((-58.5207 -34.62357, -58.52118 -34.62...  
333    POLYGON ((-58.45499 -34.57061, -58.45388 -34.5...  
...                                                  ...  
65357  POLYGON ((-58.45379 -34.55889, -58.45453 -34.5...  
65432  POLYGON ((-58.40225 -34.61876, -58.40246 -34.6...  
66039  POLYGON ((-58.45564 -34.57637, -58.4564 -34.57...  
66220  POLYGON ((-58.44489 -34.56996, -58.44411 -34.5...  
66465  POLYGON ((-58.46262 -34.63283, -58.46278 -34.6...  

[3820 rows x 12 columns]

In [13]:
gdf[['cpr','jur']].drop_duplicates()

cpr                                                jur
0     06                                       Buenos Aires
2     30                                         Entre Ríos
7     34                                            Formosa
19    22                                              Chaco
20    58                                            Neuquén
21    74                                           San Luis
39    02                    Ciudad Autónoma de Buenos Aires
74    18                                         Corrientes
105   14                                            Córdoba
120   90                                            Tucumán
130   42                                           La Pampa
158   82                                           Santa Fe
170   66                                              Salta
219   78                                         Santa Cruz
224   26                                             Chubut
225   54                                           Misiones
253   86                                Santiago del Estero
341   38                                              Jujuy
416   46                                           La Rioja
495   62                                          Río Negro
955   70                                           San Juan
1021  50                                            Mendoza
2631  10                                          Catamarca
6077  94  Tierra del Fuego, Antártida e Islas del Atlánt...

In [14]:
URL_DICCIONARIO = 'https://cdn.buenosaires.gob.ar/datosabiertos/datasets/transporte-y-obras-publicas/viajes-etapas-transporte-publico/departamentos_exportar.csv'
dptos = pd.read_csv(URL_DICCIONARIO, sep=';')
dptos = dptos[['link_departamento','codigo_provincia']]     


In [15]:
dptos

link_departamento  codigo_provincia
0                2001                 2
1                2002                 2
2                2003                 2
3                2004                 2
4                2005                 2
..                ...               ...
62               6778                 6
63               6805                 6
64               6840                 6
65               6861                 6
66               6882                 6

[67 rows x 2 columns]

In [16]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6892374 entries, 0 to 6892373
Data columns (total 17 columns):
 #   Column                      Dtype  
---  ------                      -----  
 0   id_tarjeta                  int64  
 1   id_viaje                    int64  
 2   cantidad_etapas             int64  
 3   rango_horario               int64  
 4   etapas_subte                int64  
 5   etapas_tren                 int64  
 6   etapas_colectivo            int64  
 7   longitud_origen_viaje       float64
 8   latitud_origen_viaje        float64
 9   longitud_destino_viaje      float64
 10  latitud_destino_viaje       float64
 11  departamento_origen_viaje   float64
 12  departamento_destino_viaje  float64
 13  factor_expansion_viaje      float64
 14  etapas_incompletas          object 
 15  genero                      object 
 16  grupo_edad                  float64
dtypes: float64(8), int64(7), object(2)
memory usage: 893.9+ MB


In [17]:
import h3
from typing import Optional

def add_h3_index(
    df: pd.DataFrame,
    lat_col: str = "lat",
    lon_col: str = "long",
    resolution: int = 10,
    out_col: Optional[str] = None,
    inplace: bool = False,
) -> pd.Series | pd.DataFrame:
    """
    Calcula el índice H3 por fila a partir de lat/lon usando h3.latlng_to_cell.

    - Si inplace=False (default): devuelve una Series (1D) con los H3.
    - Si inplace=True: agrega la columna al DataFrame y devuelve el DataFrame.

    out_col:
      - Si None, usa f"h3_res{resolution}"
    """
    if out_col is None:
        out_col = f"h3_res{resolution}"

    if lat_col not in df.columns or lon_col not in df.columns:
        raise KeyError(f"Faltan columnas requeridas: {lat_col=} {lon_col=}")

    lat = df[lat_col]
    lon = df[lon_col]
    mask = lat.notna() & lon.notna()

    h3_series = pd.Series(index=df.index, dtype="object", name=out_col)
    if mask.any():
        # Más rápido que df.apply(axis=1)
        cells = [
            h3.latlng_to_cell(float(la), float(lo), resolution)
            for la, lo in zip(lat[mask].to_numpy(), lon[mask].to_numpy())
        ]
        h3_series.loc[mask] = cells

    if inplace:
        df[out_col] = h3_series
        return df

    return h3_series

def h3_parent_mapping(h3_index: str, parent_res: int) -> Optional[str]:
    """Obtiene el hexágono padre de una resolución menor."""
    try:
        return h3.cell_to_parent(h3_index, parent_res)
    except:
        return None

In [18]:
H3RESOL = 10
df['origen_h3_r10'] = add_h3_index(df, lat_col='latitud_origen_viaje', lon_col='longitud_origen_viaje', resolution=H3RESOL)
df['destino_h3_r10'] = add_h3_index(df, lat_col='latitud_destino_viaje', lon_col='longitud_destino_viaje', resolution=H3RESOL)

df['origen_h3_parent9'] = df['origen_h3_r10'].apply(lambda x: h3.cell_to_parent(x, 9) if pd.notna(x) else None)
df['destino_h3_parent9'] = df['destino_h3_r10'].apply(lambda x: h3.cell_to_parent(x, 9) if pd.notna(x) else None)


In [23]:
conteo_agrupado = df.groupby('origen_h3_parent9')['factor_expansion_viaje'].sum().astype(int)
print("Conteo ponderado de registros por celda h3:")
print(conteo_agrupado)

Conteo ponderado de registros por celda h3:
origen_h3_parent9
89c2e0221afffff     0
89c2e024013ffff     4
89c2e024017ffff     1
89c2e02401bffff     2
89c2e024043ffff     1
                   ..
89c2eedb56fffff     9
89c2eedb587ffff    60
89c2eedb58fffff    26
89c2eedb5bbffff     5
89c2eedb643ffff    80
Name: factor_expansion_viaje, Length: 14701, dtype: int64


In [ ]:
import folium
import h3
import pandas as pd

# 1. Preparar datos
stats = df.groupby('origen_h3_parent9')['factor_expansion_viaje'].sum().reset_index()
stats.columns = ['h3_index', 'weighted_count']

# 2. Generar el GeoJSON manualmente
features = []
for idx, row in stats.iterrows():
    h3_index = row['h3_index']
    
    # En H3 v4, cell_to_boundary devuelve ((lat, lng), (lat, lng), ...)
    boundary = h3.cell_to_boundary(h3_index)
    
    # Invertimos el orden a [lng, lat] para que sea compatible con GeoJSON/Folium
    flipped_boundary = [[lng, lat] for lat, lng in boundary]
    
    # IMPORTANTE: GeoJSON requiere que el polígono se "cierre" 
    # repitiendo el primer punto al final.
    flipped_boundary.append(flipped_boundary[0])
    
    feature = {
        'type': 'Feature',
        'id': h3_index,
        'geometry': {
            'type': 'Polygon',
            'coordinates': [flipped_boundary]
        },
        'properties': {
            'h3_index': h3_index,
            'weighted_count': float(row['weighted_count'])
        }
    }
    features.append(feature)

geojson_data = {
    'type': 'FeatureCollection',
    'features': features
}

# 3. Crear el mapa
m = folium.Map(
    location=[-34.6037, -58.3816],
    zoom_start=11,
    tiles='cartodbpositron'
)

# 4. Capa Coroplética
folium.Choropleth(
    geo_data=geojson_data,
    data=stats,
    columns=['h3_index', 'weighted_count'],
    key_on='feature.id',
    fill_color='YlOrRd',
    fill_opacity=0.6,
    line_opacity=0.4, # Un poco más marcado para ver los hexágonos
    legend_name='Viajes Ponderados'
).add_to(m)


m.save('mapa_trips.html')


In [ ]:
# https://github.com/nlebovits/ciut-redatam?tab=readme-ov-file
# https://www.indec.gob.ar/indec/web/Institucional-Indec-BasesDeDatos-6

In [ ]:
import duckdb
import pandas as pd
import geopandas as gpd

# Configurar DuckDB
con = duckdb.connect()
for cmd in [
    "INSTALL spatial",
    "LOAD spatial", 
    "INSTALL httpfs",
    "LOAD httpfs"
]:
    con.execute(cmd)




In [ ]:

query = """
SELECT distinct 
    codigo_variable
FROM 's3://arg-fulbright-data/censo-argentino-2022/censo-2022-largo.parquet'
"""

variables = con.execute(query).fetchdf()
variables   

In [ ]:

# PERSONA_EDADQUI #Edad en grupos quinquenales
# PERSONA_P02 # Sexo registrado al nacer


In [ ]:

query_gender = """
SELECT 
    id_geo,
    etiqueta_categoria,
    SUM(conteo) AS total_conteo
FROM 's3://arg-fulbright-data/censo-argentino-2022/censo-2022-largo.parquet'
WHERE codigo_variable = 'PERSONA_P02'
  AND valor_provincia = '02'
GROUP BY id_geo, etiqueta_categoria
ORDER BY id_geo, etiqueta_categoria;
"""

census_gender = con.execute(query_gender).fetchdf()
  

In [ ]:
census_gender

https://censo.gob.ar/index.php/datos_definitivos_caba/

In [ ]:
import duckdb
import pandas as pd
import geopandas as gpd

# Configurar DuckDB
con = duckdb.connect()
for cmd in [
    "INSTALL spatial",
    "LOAD spatial", 
    "INSTALL httpfs",
    "LOAD httpfs"
]:
    con.execute(cmd)


query_age = """
SELECT 
    id_geo,
    etiqueta_categoria as tramo_edad,
    SUM(conteo) AS total_conteo
FROM 's3://arg-fulbright-data/censo-argentino-2022/censo-2022-largo.parquet'
WHERE codigo_variable = 'PERSONA_EDADQUI'
  AND valor_provincia = '02'
GROUP BY id_geo, etiqueta_categoria
ORDER BY id_geo, etiqueta_categoria;
"""

census_age = con.execute(query_age).fetchdf()


# Ahora vamos a proyectar la cantidad de hombres y mujeres por tramo etario 
# usando las tasas de feminidad en CABA para el Censo 2022.
# https://censo.gob.ar/index.php/datos_definitivos_caba/
# DataFrame de Tasas de Feminidad (Armado a mano con los datos del archivo)
# https://censo.gob.ar/wp-content/uploads/2023/11/c2022_caba_est_c4_1.xlsx

# Tasas de feminidad por tramo etario en CABA
data_tasas = {
    'tramo_edad': [
        '00 A 04', '05 A 09', '10 A 14', '15 A 19', '20 A 24', '25 A 29', '30 A 34', '35 A 39',
        '40 A 44', '45 A 49', '50 A 54', '55 A 59', '60 A 64', '65 A 69', '70 A 74',
        '75 A 79', '80 A 84', '85 A 89', '90 A 94', '95 A 99', '100 Y MÁS'
    ],
    'tasa_feminidad': [
        97, 97, 97, 101, 108, 109, 108, 106,
        110, 115, 118, 123, 126, 137, 147,
        163, 187, 223, 290, 370, 557
    ]
}

df_tasas = pd.DataFrame(data_tasas)


# Vamos a recategorizar los tramos de edad más altos de la información de cada radio censal
# para que coincidan con los datos de tasas de feminidad.
census_age['tramo_edad'] = census_age['tramo_edad'].replace(
    {'100 A 104': '100 Y MÁS', '105 Y MÁS': '100 Y MÁS'}
)

# Group by id_geo and etiqueta_categoria to unify the counts
census_age = census_age.groupby(['id_geo', 'tramo_edad'], as_index=False)['total_conteo'].sum()


# Ahora hacemos un merge de census_age con df_tasas para luego calcular las proyecciones 
# de hombres y mujeres en cada radio censal y tramo etario.
census_age_by_gender = census_age.merge(df_tasas, left_on='tramo_edad', right_on='tramo_edad', how='left')

# Calculamos la cantidad de hombres y mujeres usando la tasa de feminidad
# Fórmula: Tasa Fem = (Mujeres / Hombres) * 100
# Total = Mujeres + Hombres
# Hombres = Total / (1 + (Tasa Fem / 100))
census_age_by_gender['hombres_float'] = census_age_by_gender['total_conteo'] / (1 + (census_age_by_gender['tasa_feminidad'] / 100))
# Redondeamos hombres al entero más cercano
census_age_by_gender['hombres'] = census_age_by_gender['hombres_float'].round().astype(int)
# Mujeres = Total - Hombres
census_age_by_gender['mujeres'] = census_age_by_gender['total_conteo'] - census_age_by_gender['hombres']

# chequeamos que la suma de hombres y mujeres dé el total original en cada radio censal y grupo etario
check = (census_age_by_gender['hombres'] + census_age_by_gender['mujeres']) == census_age_by_gender['total_conteo']
print(f"Registros con errores de suma: {len(check) - check.sum()}")

# Limpieza de columnas auxiliares
census_age_by_gender = census_age_by_gender.drop(columns=['hombres_float'])

In [ ]:
census_age_by_gender

In [ ]:
PROCESSED_DATA_DIR = Path("data/processed")

pop_reach_h3 = pd.read_parquet(PROCESSED_DATA_DIR / "population_reach_h3.parquet")



In [ ]:
pop_reach_h3